In [1]:
import json
#import spacy
#import en_core_sci_lg
#from spacy.pipeline import EntityRuler
import re
import pandas as pd

In [4]:
"""
Input
"""

input_path = 'C:/Users/SuresMal/Documents/Coronawhy/data/cord19/processed/'
merged_text_vec_csv_path = '%scord_titles_abstracts_conclusions_180720.csv' % input_path

drug_terms_path = 'C:/Users/SuresMal/Documents/GitHub/drug-lit-contradictory-claims/tests/data/resources/DrugNames.txt'


"""
Output
"""

output_path = 'C:/Users/SuresMal/Documents/Coronawhy/data/cord19/processed/'

section_text_with_drugs_outpath = '%ssection_text_with_drug_mentions_180720.csv' %output_path
section_text_with_drugs_ann_outpath = '%ssection_text_with_drug_mentions_ann_180720.csv' %output_path

In [5]:
#nlp = en_core_sci_lg.load()

merged_text_vec_df = pd.read_csv(merged_text_vec_csv_path, index_col=0)

In [7]:
"""
Merge all sentences belonging to each section of each paper into contiguous text passages.
"""

merged_text_vec_df

concat_sent_df = merged_text_vec_df.groupby(['cord_uid', 'section'], as_index=False).agg({'sentence': ' '.join})
concat_sent_df.loc[:, 'sentence'] = concat_sent_df.loc[:, 'sentence'].str.lower()

concat_sent_df= concat_sent_df.rename(columns={'sentence' :'text'})

In [6]:
"""
Read drug terms from reference file and generate regex pattern for matching.
"""

with open(drug_terms_path) as f:
    drug_terms = ['%s' % i.lower() for i in f.read().splitlines()]
    
drug_terms_pattern =  '\W' + '\W|\W'.join(drug_terms) + '\W'

In [8]:
drug_terms_pattern

"\\W.alpha.-amylcinnamaldehyde\\W|\\W.alpha.-cellulose\\W|\\W.alpha.-glucan oligosaccharide\\W|\\W.alpha.-hexylcinnamaldehyde\\W|\\W.alpha.-isobutylphenethyl alcohol\\W|\\W.alpha.-lipoic acid\\W|\\W.alpha.-tocopherol\\W|\\W.alpha.-tocopherol acetate\\W|\\W.alpha.1-proteinase inhibitor human\\W|\\W.beta.-alanine\\W|\\W.beta.-bisabolol\\W|\\W.beta.-carotene\\W|\\W.beta.-sitosterol\\W|\\W.beta.-thujaplicin\\W|\\W.beta.-tocopherol\\W|\\W.gamma.-aminobutyric acid\\W|\\W.gamma.-decalactone\\W|\\W.gamma.-nonalactone\\W|\\W.gamma.-octalactone\\W|\\W.gamma.-undecalactone\\W|\\W1-butene\\W|\\W1-decene\\W|\\W1-glyceryl monooleate\\W|\\W1-methyl-2-pyrrolidinone\\W|\\W1-myristylpicolinium\\W|\\W1-octanol\\W|\\W1-p-menthene-8-thiol\\W|\\W1-propanol\\W|\\W1-propoxy-2-propanol\\W|\\W1-tetradecene\\W|\\W1-vinyl-2-pyrrolidone\\W|\\W10-hydroxycapric acid\\W|\\W10-hydroxydecanoic acid\\W|\\W12-hydroxystearic acid\\W|\\W17-alpha-hydroxyprogesterone\\W|\\W2-acrylamido-2-methyl-1-propanesulfonic acid\\W|\\W2

In [9]:
"""
Filter to rows where section text contains drug term regex pattern.
"""

contain_drug_mask = concat_sent_df['text'].str.contains(drug_terms_pattern, case=False)
section_text_with_drugs_df = concat_sent_df[contain_drug_mask]

In [10]:
section_text_with_drugs_df.to_csv(section_text_with_drugs_outpath)

In [11]:
print('Number of papers after filtering for drug mentions:',len(section_text_with_drugs_df.cord_uid.unique()))

Number of papers after filtering for drug mentions: 3745


In [12]:
title_data = section_text_with_drugs_df.loc[section_text_with_drugs_df.section.str.lower()=='title',:]
abstract_data = section_text_with_drugs_df.loc[section_text_with_drugs_df.section.str.lower()=='abstract',:]
conclusion_data = section_text_with_drugs_df.loc[(section_text_with_drugs_df.section.str.lower()!='title') & (section_text_with_drugs_df.section.str.lower()!='abstract'),:]

In [13]:
print('Number of papers:', section_text_with_drugs_df.cord_uid.nunique())
print('Number of papers with title:', title_data.cord_uid.nunique())
print('Number of papers with abstract:', abstract_data.cord_uid.nunique())
print('Number of papers with conclusion:', conclusion_data.cord_uid.nunique())

Number of papers: 3745
Number of papers with title: 0
Number of papers with abstract: 1374
Number of papers with conclusion: 3147


In [14]:
#v31 output
print('Number of papers:', section_text_with_drugs_df.cord_uid.nunique())
print('Number of papers with title:', title_data.cord_uid.nunique())
print('Number of papers with abstract:', abstract_data.cord_uid.nunique())
print('Number of papers with conclusion:', conclusion_data.cord_uid.nunique())

Number of papers: 2564
Number of papers with title: 0
Number of papers with abstract: 978
Number of papers with conclusion: 2116


In [8]:
"""
Manual annotation of drug terms used.

"""

section_text_with_drugs_ann_df = section_text_with_drugs_df.copy()

section_text_with_drugs_ann_df['drug_terms_used'] = ''

for index, row in section_text_with_drugs_ann_df.iterrows():
    
    drugs_used = []
    for drug in drug_terms:
        if drug in row.text:
            drugs_used.append(drug)
    
    section_text_with_drugs_ann_df.at[index, 'drug_terms_used'] = ','.join(drugs_used)
    
#section_text_with_drugs_ann_df.to_csv(section_text_with_drugs_ann_outpath)

In [16]:
section_text_with_drugs_ann_df

cord_uid                                            section  \
26     019rcbpg  Potential biological mechanisms of SARS-CoV-2 ...   
30     01es0zv4                                           Abstract   
31     01es0zv4                                         CONCLUSION   
32     01es0zv4                                        CONCLUSION:   
39     01lyavy2                                           Abstract   
...         ...                                                ...   
28040  zrg2z17n                                           Abstract   
28070  zsz9xnxt                                         Discussion   
28094  zv0ysi8m                                           Abstract   
28095  zv0ysi8m                                        Conclusions   
28121  zwqci59h                                         Discussion   

                                                    text  \
26     there are indications in the literature of a n...   
30     coronavirus disease 2019 has become a global p...   
31     covid-19 is a pandemic with high morbidity and...   
32     covid-19 is a pandemic with high morbidity and...   
39     then, the really positive treatment could be t...   
...                                                  ...   
28040  the covid-19 pandemic has claimed over 150,000...   
28070  we demonstrate that mechanically ventilated pa...   
28094  sars-cov-2 is a novel strain of coronavirus th...   
28095  sars-cov-2 has been declared a pandemic that c...   
28121  although recent studies have reported epidemio...   

                                         drug_terms_used  
26                                             ifn-gamma  
30     chloroquine,lopinavir,remdesivir,ritonavir,azi...  
31     chloroquine,lopinavir,remdesivir,ritonavir,azi...  
32     chloroquine,lopinavir,remdesivir,ritonavir,azi...  
39                                             protein s  
...                                                  ...  
28040                                          vitamin d  
28070                                     carbon dioxide  
28094     chloroquine,favipiravir,remdesivir,chloroquine  
28095     chloroquine,favipiravir,remdesivir,chloroquine  
28121  compro,cyclosporine,methylprednisolone,prednis...  

[3943 rows x 4 columns]

In [9]:
"""
Manual checking for drug mentions excluded by regex search, using direct string matches.

"""

sections_texts = concat_sent_df.text.tolist()

cord_uids_contain_drugs_manual_search_dict = {}

idx = 0
for idx, row in concat_sent_df.iterrows():
    text = row.text
    for drug in drug_terms:
        if drug in text:
            cord_uids_contain_drugs_manual_search_dict.setdefault(row.cord_uid, []).append(drug)
            
    idx +=1
    
cord_uids_with_manual_search_drugs = set(cord_uids_contain_drugs_manual_search_dict.keys())

#Difference in cord_uid lists
diff_cord_uids = cord_uids_with_manual_search_drugs - set(section_text_with_drugs_df.cord_uid)

In [10]:
len(diff_cord_uids)

3517

In [21]:
#diff_cord = 'px0twvhs'
drugs_used = []
ignore_drugs = ['stimate','collagen','ultane','differin']

for diff_cord in diff_cord_uids:
    drugs = cord_uids_contain_drugs_manual_search_dict[diff_cord]
    drugs_used = drugs_used + drugs
    test_df = concat_sent_df.loc[concat_sent_df.cord_uid == diff_cord]

    for i,sent in enumerate(test_df.text.tolist()):
        if (drugs[0] in sent) and any(d in drugs for d in ignore_drugs)==False:
            print(i,drugs,'\n',sent)

drugs_used = list(set(drugs_used))
"""
Correctly excluded:
1. stimate -> estimate
2. collagen -> collagenous
3. ultane -> simultaneouly
4. differin -> differing
5. proper -> propelling
6. compro -> compromised
7. cialis -> specialist
8. lustra -> illustrate
8. rective -> directive (/corrective)
9. ultiva -> multivariate
10. ambien -> ambient
11. pectin -> expecting?

Incorrectly excluded:
6. fibrinogen -> fibrinogens
7. choline -> cholinergic

"""

2 ['propel'] 
 as the sars-cov-2 pandemic progresses, knowledge of how to prevent its spread is of utmost concern. with the rapid dissemination globally of the virus, anecdotal evidence from experiences in wuhan, china, as well as historical literature from similar viral epidemics (mers-cov, h1n1, sars) has guided otolaryngology protocols. [11] [12] [13] [14] as of the time of this publication, conflicting information persists among regulatory bodies as to degree of protection required for aerosol-generating procedures. 15, 16 while available evidence seems to suggest that spread is primarily through respiratory droplets, there is no consensus on exact transmission and little research available attempting to evaluate risk of specific otolaryngologic procedures. in otolaryngology clinical practice, many procedures involve instrumentation and examination of areas suspected to carry high viral loads: the nose, nasopharynx, and oropharynx. 17 as practitioners begin to entertain a reverse s

2 ['acticin'] 
 during the covid-19 pandemic, intubation is the highest risk ed procedure, 6,7 ,8,9 and continuing cpr during intubation likely increases exposure risk. non-compression intubation is suggested by ed resuscitation experts and the american heart association (aha) to minimize covid-19 exposure to staff. before this pandemic, compression interruption was anathema except for ventilation and pulse and rhythm checks. 10 considering the risks to staff, novel approaches to intubation during cardiac arrests should be considered. to avoid unknown and high-risk exposures, our ed currently treats all cardiac arrests as if covid-19 positive. prior to ems arrival, our ed staff dons airborne ppe consisting of an n95 respirator, goggles, gown, and gloves. 11 additionally, those managing the airway and those performing compressions don papr hoods. 12 all cardiac arrests are resuscitated in our negative pressure decon room. 13 theoretically, once intubated with the ett cuff inflated and v

0 ['compro', 'compro'] 
 a number of experimental and clinical evidences support the hypothesis that sars-cov-2 can be found in tears, and that it can therefore be received and transmitted through this route. although it seems at the moment that the virus cannot be detected in the conjunctival sac of infected patients without conjunctivitis [21], and that there is a low risk of coronavirus spreading through tears [22], nevertheless sars-cov-2 may survive for a long time or replicate in the conjunctiva, after conjunctivitis signs vanished. therefore, eye protection (protective goggles alone or in association with face shield) are necessary to prevent eye exposure to contaminated droplets and bioaerosol emitted by patients not only by cough and sneeze, but also by breathing [23,24,25]. obviously, eye care providers and technicians may be more susceptible to infection due to the nature and proximity of the ophthalmic examination [26]. eye care providers are encouraged to use slit lamp bre

0 ['retrovir'] 
 the sars-cov-2 virus has resulted in a devastating pandemic of covid-19. exploring compounds that could offer a breakthrough in treatment is the need of the hour. re-positioning cheap, freely available and safe drugs is a priority. the paper proposes evidence for the potential use of diethylcarbamazine (dec) in the treatment of covid-19. dec has inhibitory effects on arachidonic acid metabolism to prostaglandins, little known anti-viral effects on animal retroviruses and demonstrated anti-inflammatory actions in animal models of lung inflammation indicating the need to explore this hypothesis further. we believe this is the first time dec is being proposed to treat covid-19.
1 ['protein s'] 
 bats are known to be the reservoirs of many deadly viruses like the nipa virus and ebola beside coronaviruses. a reason for this is the inability of bats' innate immunity to sense viral dnas in the cytosol. bats have a very high rate of metabolism and increased rates of oxidative 

2 ['cialis'] 
 considering the 5 years from 2015 to 2019, the proportion of severe cases requiring intensive care and the case fatality ratios were strikingly similar among covid-19 and german pneumonia patients. however, based on these data, covid-19 may affect a younger cohort, which seems not fully explained by the different age structure of the chinese population. as reported by the china centre for disease control and prevention, there seems to be a higher risk for severe disease in older ages and in patients with chronic grey line: proportion of icu in pneumonia sentinel patients. data from five covid-19 series [5, 6, 9, 11, 12] . grey line: proportion of ventilation in pneumonia sentinel patients. data from five covid-19 series [5, 6, [9] [10] [11] . considering the 5 years from 2015 to 2019, the proportion of severe cases requiring intensive care and the case fatality ratios were strikingly similar among covid-19 and german pneumonia patients. however, based on these data, covi

...

0 ['protein s', 'protein s'] 
 the experimental affinity measurements (e.g., surface plasmon resonance (spr)) confirm the high affinity of sars-2002 rbd–ace2 binding, with an equilibrium dissociation constant (kd) of ~1.5–10.0 nm [25,26,27], comparable to the binding affinity of ace2 and the covid-19 rbd (kd = ~1.2–14.7 nm [27,28]) and consistent with our md-based calculation (figure 1a, figure s3, and table s2). while we relied on the modeled covid-19 rbd–ace2 interaction, the median interaction score of the complex (−1928.8), based on the md simulation starting from the recently published x-ray structure (pdb 6lzg [21]), was even closer to the sars-2002 rbd–ace2 score (−1929.5). binding affinity is achieved through a combination of interface contact optimization and protein stability (figure 3e). while the rbd–ace2 complex can be resolved at high-resolution by cryo-em [24] and x-ray crystallography, md simulations provide orthogonal information about the interaction dynamics on a nan

1 ['ellence'] 
 while evidence is rapidly emerging about covid-19-associated coagulopathy and thrombosis risk, there is little high-quality evidence to guide antithrombotic management. the present recommendations aim to provide guidance for frontline clinicians caring for patients with covid-19 and/ or patients with chronic thrombotic conditions requiring ongoing management in the era of the covid-19 pandemic. whenever possible, we recommend that clinicians rely on pre-covid evidence-based principles of anticoagulation management combined with rational approaches to address unprecedented clinical challenges. as this area is rapidly evolving, it will be necessary to integrate additional evidence into our management recommendations. fortunately, several clinical studies, including randomized controlled trials, are being conducted; the results will better inform our management decisions. online resources, such as the anticoagulation forum centers of excellence resource center (https ://ac

0 ['cialis', 'pectin'] 
 we describe the basic we describe the basic principles of mental health care during the covid-19 pandemic that should be endorsed by the mental health professional associations and incorporated in the health strategies for the management of the covid-19 pandemic. the main principle is that there should be no substantial differences in the provision of health care for covid-19 between persons with pre-existing mental health disorders and the ones without previous disorders. subsequently, the organization of the health care should reflect that as well. these principles should (a) prevent the possible effects of stigmatizing attitudes toward mental health issues, possibly leading to potentially deleterious situations, such as psychiatric patients being treated (even temporarily) separately from other patients, in psychiatric facilities, where the staff is not equipped and trained adequately for the management of covid-19; (b) highlight the fact that patients with 

3 ['lustra'] 
 after investigating the motion of bioaerosol particles, it was clear that airflow was the main factor determining their trajectory. since the bls-3 laboratory was modeled with an up-supply and up-return ventilation mode, it can be predicted that bioaerosol particles will undergo complex migration in three-dimensional space under the function of airflow combined with obstacles. to visualize the spread of bioaerosol particles under the control of airflow, three-dimensional concentration iso-surface maps were employed to determine migration characteristics. 
fig. 7
illustrates the migration pattern of bioaerosol particles in the bsl-3 laboratory with a velocity streamline map and a three-dimensional concentration iso-surface map. after bioaerosol particles are released from the source, they would be controlled by the vertical airflow and moved downward. ten seconds later, a cloud of high-concentration particles would hit the ground and move in two directions, as affected by

'\nCorrectly excluded:\n1. stimate -> estimate\n2. collagen -> collagenous\n3. ultane -> simultaneouly\n4. differin -> differing\n\nIncorrectly excluded:\n\n'

In [22]:
drugs_used

['protein s',
 'propel',
 'rectiv',
 'ting af',
 'elimite',
 'propanol',
 'thrive',
 'influenza a virus',
 'retrovir',
 'heparin',
 'differin',
 'prednisone',
 'choline',
 'contrave',
 'emodin',
 'sojourn',
 'glycyrrhizin',
 'merrem',
 'biotin',
 'acular',
 'proline',
 'totect',
 'cysteine',
 'lustra',
 'renova',
 'ricola',
 'stimate',
 'flavor',
 'sorine',
 'aspirin',
 'turalio',
 'ethylene',
 'convalescent plasma',
 'propylene',
 'ms contin',
 'testim',
 'lactate',
 'cambia',
 'multigen',
 'econtra',
 'l-formula',
 'ellence',
 'hyper-sal',
 'astelin',
 'thiola',
 'tenuate',
 'ambien',
 'dopamine',
 'acetic acid',
 'angiotensin ii',
 'phenol',
 'aspartate',
 'my choice',
 'pectin',
 'collagen',
 'take action',
 'nitric oxide',
 'hydroxychloroquine',
 'intrinsic factor',
 'coagulation factor ii',
 'augmentin',
 'cresol',
 'estring',
 'acticin',
 'pentam',
 'inositol',
 'alanine',
 'evicel',
 'ovidrel',
 'vasocon',
 'ivermectin',
 'hemofil',
 'chloride ion',
 'factive',
 'glutaral',
 'b

In [23]:
len(drugs_used)

114